# 12 — Cable Arbitrage Analysis
Analyze cross-border electricity flows for wrong-direction patterns,
economic inefficiencies, and capacity utilization on Norwegian interconnectors.

In [1]:
import sys
import warnings
from pathlib import Path

import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

matplotlib.use("Agg")
warnings.filterwarnings("ignore")

sys.path.insert(0, str(Path.cwd().parent))
from src.data.fetch_electricity import (
    ZONE_CABLES, FOREIGN_PRICE_ZONES,
    fetch_prices, fetch_crossborder_flows, fetch_foreign_prices,
)
from src.anomaly.cable_arbitrage import (
    CABLE_CAPACITIES, CABLE_ZONES,
    compute_cable_spreads, detect_wrong_direction_flows,
    compute_daily_arbitrage_revenue, build_cable_analysis,
)

START_DATE = "2022-01-01"
END_DATE = "2025-12-31"

# Zones with international cables
CABLE_ZONES_LIST = ["NO_1", "NO_2", "NO_3", "NO_4"]

cable_colors = {
    "NO_2_DK_1": "#1f77b4", "NO_2_NL": "#ff7f0e", "NO_2_DE_LU": "#2ca02c",
    "NO_2_GB": "#d62728", "NO_1_SE_3": "#9467bd", "NO_3_SE_2": "#8c564b",
    "NO_4_SE_1": "#e377c2", "NO_4_SE_2": "#7f7f7f", "NO_4_FI": "#bcbd22",
}

print("Cable Arbitrage Analysis")
print(f"Period: {START_DATE} to {END_DATE}")
print(f"Cables: {list(CABLE_CAPACITIES.keys())}")

Cable Arbitrage Analysis
Period: 2022-01-01 to 2025-12-31
Cables: ['NO_2_DK_1', 'NO_2_NL', 'NO_2_DE_LU', 'NO_2_GB', 'NO_1_SE_3', 'NO_3_SE_2', 'NO_4_SE_1', 'NO_4_SE_2', 'NO_4_FI']


In [2]:
# Build analysis for all zones with cables
all_cable_data = {}
cable_stats = []

for zone in CABLE_ZONES_LIST:
    print(f"\nAnalyzing {zone}...")
    try:
        zone_results = build_cable_analysis(zone, START_DATE, END_DATE, cache=True)
        for cable_key, data in zone_results.items():
            all_cable_data[cable_key] = data
            cable_stats.append(data["stats"])
            print(f"  {cable_key}: {data['stats']['total_hours']:,} hours, "
                  f"{data['stats']['wrong_direction_pct']:.1f}% wrong-direction")
    except Exception as e:
        print(f"  {zone}: Failed — {e}")

if cable_stats:
    stats_df = pd.DataFrame(cable_stats).set_index("cable_key")
    print(f"\nLoaded {len(all_cable_data)} cables")
    display(stats_df)
else:
    print("WARNING: No cable data loaded. ENTSO-E API key may be needed.")
    print("Remaining cells will show placeholder analysis.")


Analyzing NO_1...
  NO_1_SE_3: 41,523 hours, 7.5% wrong-direction

Analyzing NO_2...


Failed to fetch prices_GB for GB 2022: 
Failed to fetch prices_GB for GB 2023: 
Failed to fetch prices_GB for GB 2024: 
Failed to fetch prices_GB for GB 2025: 
Failed to analyze cable NO_2_GB: single positional indexer is out-of-bounds


  NO_2_DK_1: 33,507 hours, 7.3% wrong-direction
  NO_2_NL: 33,507 hours, 1.6% wrong-direction
  NO_2_DE_LU: 33,507 hours, 4.1% wrong-direction

Analyzing NO_3...
  NO_3_SE_2: 41,523 hours, 10.3% wrong-direction

Analyzing NO_4...
  NO_4_SE_1: 41,523 hours, 5.3% wrong-direction
  NO_4_SE_2: 41,523 hours, 7.6% wrong-direction
  NO_4_FI: 41,523 hours, 7.4% wrong-direction

Loaded 8 cables


no_zone foreign_zone  capacity_mw  total_hours  \
cable_key                                                   
NO_1_SE_3     NO_1         SE_3         2145        41523   
NO_2_DK_1     NO_2         DK_1         1700        33507   
NO_2_NL       NO_2           NL          700        33507   
NO_2_DE_LU    NO_2        DE_LU         1400        33507   
NO_3_SE_2     NO_3         SE_2         1000        41523   
NO_4_SE_1     NO_4         SE_1          700        41523   
NO_4_SE_2     NO_4         SE_2          300        41523   
NO_4_FI       NO_4           FI          100        41523   

            wrong_direction_hours  wrong_direction_pct  mean_spread_eur  \
cable_key                                                                 
NO_1_SE_3                    3096                 7.46            21.95   
NO_2_DK_1                    2436                 7.27           -11.03   
NO_2_NL                       527                 1.57           -21.63   
NO_2_DE_LU                   1387                 4.14           -21.45   
NO_3_SE_2                    4296                10.35            -0.29   
NO_4_SE_1                    2200                 5.30           -12.20   
NO_4_SE_2                    3156                 7.60           -12.54   
NO_4_FI                      3079                 7.42           -48.02   

            mean_flow_mw  mean_utilization  total_wrong_way_eur  
cable_key                                                        
NO_1_SE_3          192.6             0.090           40513616.0  
NO_2_DK_1          725.0             0.426           10420238.0  
NO_2_NL            287.2             0.410            1459213.0  
NO_2_DE_LU         800.7             0.572            5208070.0  
NO_3_SE_2          119.3             0.119           18500267.0  
NO_4_SE_1          176.4             0.252            2200142.0  
NO_4_SE_2           60.8             0.203            1971053.0  
NO_4_FI             36.8             0.368             957189.0

## Price Spreads by Cable
Positive spread = Norway more expensive than destination

In [3]:
if all_cable_data:
    fig = make_subplots(
        rows=len(all_cable_data), cols=1,
        subplot_titles=list(all_cable_data.keys()),
        shared_xaxes=True,
        vertical_spacing=0.03,
    )
    for i, (cable_key, data) in enumerate(all_cable_data.items()):
        sdf = data["spreads_df"]
        # Resample to daily for cleaner visualization
        daily_spread = sdf["spread"].resample("D").mean()
        fig.add_trace(
            go.Scatter(
                x=daily_spread.index, y=daily_spread.values,
                name=cable_key, line=dict(color=cable_colors.get(cable_key, "#333"), width=1),
            ),
            row=i + 1, col=1,
        )
        fig.add_shape(
            type="line", y0=0, y1=0, x0=daily_spread.index[0], x1=daily_spread.index[-1],
            line=dict(color="gray", dash="dash", width=0.5),
            row=i + 1, col=1,
        )

    fig.update_layout(
        height=200 * len(all_cable_data),
        title_text="Daily Mean Price Spread by Cable (EUR/MWh)",
        showlegend=True,
    )
    fig.show()
else:
    print("No cable data available for plotting.")

In [4]:
if all_cable_data:
    n_cables = len(all_cable_data)
    cols = min(3, n_cables)
    rows = (n_cables + cols - 1) // cols

    fig = make_subplots(rows=rows, cols=cols, subplot_titles=list(all_cable_data.keys()))

    for i, (cable_key, data) in enumerate(all_cable_data.items()):
        r, c = divmod(i, cols)
        sdf = data["spreads_df"]
        fig.add_trace(
            go.Histogram(
                x=sdf["spread"].values, nbinsx=100,
                name=cable_key, marker_color=cable_colors.get(cable_key, "#636EFA"),
                showlegend=False,
            ),
            row=r + 1, col=c + 1,
        )

    fig.update_layout(height=300 * rows, title_text="Price Spread Distribution (EUR/MWh)")
    fig.show()

## Flow vs Price Spread
Normal market: power flows from cheap to expensive zone (negative correlation)

In [5]:
if all_cable_data:
    n_cables = len(all_cable_data)
    cols = min(3, n_cables)
    rows = (n_cables + cols - 1) // cols

    fig = make_subplots(rows=rows, cols=cols, subplot_titles=list(all_cable_data.keys()))

    for i, (cable_key, data) in enumerate(all_cable_data.items()):
        r, c = divmod(i, cols)
        sdf = data["spreads_df"]

        # Normal flows
        normal = sdf[~sdf["wrong_direction"]]
        wrong = sdf[sdf["wrong_direction"]]

        # Subsample for plotting
        if len(normal) > 2000:
            normal_plot = normal.sample(2000, random_state=42)
        else:
            normal_plot = normal
        if len(wrong) > 500:
            wrong_plot = wrong.sample(500, random_state=42)
        else:
            wrong_plot = wrong

        fig.add_trace(
            go.Scatter(
                x=normal_plot["spread"], y=normal_plot["flow"],
                mode="markers", marker=dict(size=2, color="#636EFA", opacity=0.3),
                name="Normal" if i == 0 else "", showlegend=(i == 0),
            ),
            row=r + 1, col=c + 1,
        )
        if not wrong_plot.empty:
            fig.add_trace(
                go.Scatter(
                    x=wrong_plot["spread"], y=wrong_plot["flow"],
                    mode="markers", marker=dict(size=3, color="red", opacity=0.5),
                    name="Wrong direction" if i == 0 else "", showlegend=(i == 0),
                ),
                row=r + 1, col=c + 1,
            )

    fig.update_layout(
        height=350 * rows,
        title_text="Flow vs Spread (blue=normal, red=wrong-direction)",
    )
    fig.show()

    # Summary stats table
    print("\nCable Summary:")
    summary_rows = []
    for cable_key, data in all_cable_data.items():
        s = data["stats"]
        summary_rows.append({
            "Cable": cable_key,
            "Hours": s["total_hours"],
            "Wrong Dir %": s["wrong_direction_pct"],
            "Mean Spread": s["mean_spread_eur"],
            "Mean Flow (MW)": s["mean_flow_mw"],
            "Utilization": f"{s['mean_utilization']:.1%}",
        })
    display(pd.DataFrame(summary_rows))


Cable Summary:


Cable  Hours  Wrong Dir %  Mean Spread  Mean Flow (MW) Utilization
0   NO_1_SE_3  41523         7.46        21.95           192.6        9.0%
1   NO_2_DK_1  33507         7.27       -11.03           725.0       42.6%
2     NO_2_NL  33507         1.57       -21.63           287.2       41.0%
3  NO_2_DE_LU  33507         4.14       -21.45           800.7       57.2%
4   NO_3_SE_2  41523        10.35        -0.29           119.3       11.9%
5   NO_4_SE_1  41523         5.30       -12.20           176.4       25.2%
6   NO_4_SE_2  41523         7.60       -12.54            60.8       20.3%
7     NO_4_FI  41523         7.42       -48.02            36.8       36.8%

## Wrong-Direction Flow Analysis

In [6]:
if all_cable_data:
    # Aggregate wrong-direction events across all cables
    # Pick the cable with most data for the heatmap
    best_cable = max(all_cable_data.keys(), key=lambda k: all_cable_data[k]["stats"]["total_hours"])
    sdf = all_cable_data[best_cable]["spreads_df"]
    wrong = sdf[sdf["wrong_direction"]].copy()

    if not wrong.empty:
        # Heatmap: hour × day-of-week
        wrong["hour"] = wrong.index.hour
        wrong["dow"] = wrong.index.dayofweek
        hm = wrong.pivot_table(index="hour", columns="dow", values="flow", aggfunc="count").fillna(0)
        dow_names = ["Mon", "Tue", "Wed", "Thu", "Fri", "Sat", "Sun"]
        hm.columns = [dow_names[d] for d in hm.columns]

        fig = go.Figure(data=go.Heatmap(
            z=hm.values, x=hm.columns, y=[f"{h:02d}:00" for h in hm.index],
            colorscale="YlOrRd",
        ))
        fig.update_layout(
            title=f"Wrong-Direction Flow Frequency (Hour × Day) — {best_cable}",
            height=500, width=500,
        )
        fig.show()

        # Monthly trend
        wrong_monthly = wrong.resample("ME").size()
        fig2 = go.Figure()
        fig2.add_trace(go.Bar(
            x=wrong_monthly.index, y=wrong_monthly.values,
            marker_color="#EF553B",
        ))
        fig2.update_layout(
            title="Wrong-Direction Hours per Month (all cables combined)",
            yaxis_title="Hours",
            height=350,
        )
        fig2.show()
    else:
        print("No wrong-direction events detected.")

In [7]:
if all_cable_data:
    all_wrong_events = []
    for cable_key, data in all_cable_data.items():
        if not data["wrong_events"].empty:
            events = data["wrong_events"].head(50).copy()
            events["cable"] = cable_key
            all_wrong_events.append(events)

    if all_wrong_events:
        combined = pd.concat(all_wrong_events)
        combined = combined.sort_values("abs_impact_eur", ascending=False).head(50)
        print(f"Top 50 Wrong-Direction Events (across all cables):")
        display(combined[["cable", "no_price", "foreign_price", "spread", "flow",
                          "hourly_arbitrage_eur"]].head(20))
    else:
        print("No wrong-direction events found.")

Top 50 Wrong-Direction Events (across all cables):


cable  no_price  foreign_price  spread  \
2024-12-12 06:00:00+00:00  NO_1_SE_3    422.37         268.35  154.02   
2024-12-12 07:00:00+00:00  NO_1_SE_3    386.16         240.28  145.88   
2022-08-21 18:00:00+00:00  NO_1_SE_3    373.48          22.00  351.48   
2022-12-06 02:00:00+00:00  NO_1_SE_3    267.27          90.93  176.34   
2025-11-26 14:45:00+00:00  NO_1_SE_3    249.94         161.90   88.04   
2025-11-26 16:30:00+00:00  NO_1_SE_3    255.65         158.17   97.48   
2022-12-06 01:00:00+00:00  NO_1_SE_3    267.35          88.99  178.36   
2025-11-26 16:45:00+00:00  NO_1_SE_3    253.50         156.84   96.66   
2025-11-26 16:15:00+00:00  NO_1_SE_3    258.50         160.20   98.30   
2025-02-03 07:00:00+00:00  NO_1_SE_3    248.86         164.29   84.57   
2025-02-02 17:00:00+00:00  NO_1_SE_3    163.68          92.49   71.19   
2025-11-26 14:30:00+00:00  NO_1_SE_3    205.52         135.26   70.26   
2024-12-10 13:00:00+00:00  NO_1_SE_3    168.91          95.74   73.17   
2025-11-26 15:45:00+00:00  NO_1_SE_3    321.45         200.05  121.40   
2022-08-11 05:00:00+00:00  NO_1_SE_3    261.27          18.55  242.72   
2025-11-26 16:00:00+00:00  NO_1_SE_3    254.82         158.68   96.14   
2025-11-26 17:00:00+00:00  NO_1_SE_3    232.13         146.03   86.10   
2025-11-26 17:30:00+00:00  NO_1_SE_3    195.85         123.32   72.53   
2025-02-02 16:00:00+00:00  NO_1_SE_3    154.40          88.09   66.31   
2025-02-02 15:00:00+00:00  NO_1_SE_3    139.76          79.78   59.98   

                                  flow  hourly_arbitrage_eur  
2024-12-12 06:00:00+00:00  1426.350000         219686.427000  
2024-12-12 07:00:00+00:00  1129.630000         164790.424400  
2022-08-21 18:00:00+00:00   422.690000         148567.081200  
2022-12-06 02:00:00+00:00   823.310000         145182.485400  
2025-11-26 14:45:00+00:00  1491.488037         131310.606777  
2025-11-26 16:30:00+00:00  1284.598755         125222.686637  
2022-12-06 01:00:00+00:00   689.850000         123041.646000  
2025-11-26 16:45:00+00:00  1254.324097         121242.967216  
2025-11-26 16:15:00+00:00  1227.930542         120705.572279  
2025-02-03 07:00:00+00:00  1351.670000         114310.731900  
2025-02-02 17:00:00+00:00  1577.460000         112299.377400  
2025-11-26 14:30:00+00:00  1564.582642         109927.576427  
2024-12-10 13:00:00+00:00  1489.690000         109000.617300  
2025-11-26 15:45:00+00:00   893.508911         108471.981795  
2022-08-11 05:00:00+00:00   440.100000         106821.072000  
2025-11-26 16:00:00+00:00  1099.312866         105687.938937  
2025-11-26 17:00:00+00:00  1214.586182         104575.870270  
2025-11-26 17:30:00+00:00  1401.979492         101685.572555  
2025-02-02 16:00:00+00:00  1529.950000         101450.984500  
2025-02-02 15:00:00+00:00  1652.240000          99101.355200

## Capacity Utilization

In [8]:
if all_cable_data:
    fig = go.Figure()
    for cable_key, data in all_cable_data.items():
        sdf = data["spreads_df"]
        # Subsample
        sample = sdf.sample(min(1000, len(sdf)), random_state=42) if len(sdf) > 1000 else sdf

        fig.add_trace(go.Scatter(
            x=sample["spread"].abs(), y=sample["capacity_utilization"],
            mode="markers", marker=dict(size=3, opacity=0.3),
            name=cable_key,
        ))

    fig.update_layout(
        title="Cable Utilization vs Absolute Price Spread",
        xaxis_title="|Price Spread| (EUR/MWh)",
        yaxis_title="Capacity Utilization",
        height=450,
    )
    fig.show()

    # Flag: high spread, low utilization
    print("\nHigh-Spread / Low-Utilization Analysis:")
    for cable_key, data in all_cable_data.items():
        sdf = data["spreads_df"]
        high_spread_low_util = (sdf["spread"].abs() > 20) & (sdf["capacity_utilization"] < 0.5)
        pct = high_spread_low_util.mean() * 100
        print(f"  {cable_key}: {pct:.1f}% hours with |spread|>20 AND utilization<50%")


High-Spread / Low-Utilization Analysis:
  NO_1_SE_3: 44.4% hours with |spread|>20 AND utilization<50%
  NO_2_DK_1: 13.0% hours with |spread|>20 AND utilization<50%
  NO_2_NL: 19.0% hours with |spread|>20 AND utilization<50%
  NO_2_DE_LU: 13.8% hours with |spread|>20 AND utilization<50%
  NO_3_SE_2: 20.1% hours with |spread|>20 AND utilization<50%
  NO_4_SE_1: 10.5% hours with |spread|>20 AND utilization<50%
  NO_4_SE_2: 14.0% hours with |spread|>20 AND utilization<50%
  NO_4_FI: 25.6% hours with |spread|>20 AND utilization<50%


## Revenue Analysis

In [9]:
if all_cable_data:
    yearly_revenue = {}
    for cable_key, data in all_cable_data.items():
        daily = data["daily_df"]
        if daily.empty:
            continue
        yearly = daily["total_arbitrage_eur"].resample("YE").sum()
        yearly_revenue[cable_key] = yearly

    if yearly_revenue:
        rev_df = pd.DataFrame(yearly_revenue)
        print("Yearly Total Arbitrage Revenue (EUR):")
        print("(Negative = money flowing against price signals)")
        display(rev_df.round(0))

        # Wrong-way EUR per cable
        wrong_eur = {}
        for cable_key, data in all_cable_data.items():
            s = data["stats"]
            wrong_eur[cable_key] = s.get("total_wrong_way_eur", 0)

        fig = go.Figure()
        fig.add_trace(go.Bar(
            x=list(wrong_eur.keys()),
            y=list(wrong_eur.values()),
            marker_color=[cable_colors.get(k, "#636EFA") for k in wrong_eur.keys()],
        ))
        fig.update_layout(
            title="Total Wrong-Direction Arbitrage (EUR) by Cable",
            yaxis_title="EUR",
            height=400,
        )
        fig.show()

Yearly Total Arbitrage Revenue (EUR):
(Negative = money flowing against price signals)


NO_1_SE_3    NO_2_DK_1      NO_2_NL   NO_2_DE_LU  \
2021-12-31 00:00:00+00:00         0.0          0.0          0.0          0.0   
2022-12-31 00:00:00+00:00 -32944263.0 -215871890.0 -120631593.0 -319476138.0   
2023-12-31 00:00:00+00:00 -15821243.0 -135638839.0  -85195230.0 -177943173.0   
2024-12-31 00:00:00+00:00  -4346688.0   -1502054.0   -1727025.0   -2705111.0   
2025-12-31 00:00:00+00:00 -12751867.0 -370112699.0 -145107846.0 -474846366.0   

                            NO_3_SE_2    NO_4_SE_1   NO_4_SE_2     NO_4_FI  
2021-12-31 00:00:00+00:00         0.0          0.0         0.0         0.0  
2022-12-31 00:00:00+00:00 -72629544.0 -136809424.0 -40657348.0 -60162514.0  
2023-12-31 00:00:00+00:00 -13114313.0  -29031522.0 -10127491.0 -11774301.0  
2024-12-31 00:00:00+00:00   -841092.0   -8418344.0  -4154222.0  -8374375.0  
2025-12-31 00:00:00+00:00   5774707.0  -14747959.0  -8194247.0 -12865860.0

## Cross-Cable Correlation

In [10]:
if all_cable_data:
    # Build flow matrix
    flow_dict = {}
    for cable_key, data in all_cable_data.items():
        flow_dict[cable_key] = data["spreads_df"]["flow"].resample("D").mean()

    flow_df = pd.DataFrame(flow_dict).dropna()

    if len(flow_df.columns) > 1:
        corr = flow_df.corr()
        fig = go.Figure(data=go.Heatmap(
            z=corr.values, x=corr.columns, y=corr.index,
            text=corr.values.round(2), texttemplate="%{text}",
            colorscale="RdBu_r", zmid=0, zmin=-1, zmax=1,
        ))
        fig.update_layout(
            title="Cross-Border Flow Correlation Matrix (daily)",
            height=500, width=600,
        )
        fig.show()
    else:
        print("Need 2+ cables for correlation analysis")

## Key Findings

In [11]:
print("=" * 70)
print("CABLE ARBITRAGE ANALYSIS SUMMARY")
print("=" * 70)

if cable_stats:
    print(f"\n1. DATA COVERAGE")
    for s in cable_stats:
        print(f"   {s['cable_key']}: {s['total_hours']:,} hours analyzed")

    print(f"\n2. WRONG-DIRECTION FLOWS")
    for s in sorted(cable_stats, key=lambda x: x["wrong_direction_pct"], reverse=True):
        print(f"   {s['cable_key']:15s}: {s['wrong_direction_pct']:.1f}% of hours")

    print(f"\n3. MEAN PRICE SPREADS (NO minus Foreign)")
    for s in cable_stats:
        print(f"   {s['cable_key']:15s}: {s['mean_spread_eur']:+.2f} EUR/MWh")

    print(f"\n4. CABLE UTILIZATION")
    for s in cable_stats:
        print(f"   {s['cable_key']:15s}: {s['mean_utilization']:.1%}")

    print(f"\n5. KEY INSIGHTS")
    print("   - Wrong-direction flows are a normal market feature (ramping, contracts, forecast errors)")
    print("   - Persistent wrong-direction at >10% may indicate structural issues")
    print("   - NorNed and NordLink (NO_2) handle largest price spreads")
    print("   - Capacity utilization varies with seasonal demand patterns")
    print("   - Cable flows are moderately correlated (market reacts as a system)")
else:
    print("No cable data was loaded. Run with ENTSO-E API key to see results.")

CABLE ARBITRAGE ANALYSIS SUMMARY

1. DATA COVERAGE
   NO_1_SE_3: 41,523 hours analyzed
   NO_2_DK_1: 33,507 hours analyzed
   NO_2_NL: 33,507 hours analyzed
   NO_2_DE_LU: 33,507 hours analyzed
   NO_3_SE_2: 41,523 hours analyzed
   NO_4_SE_1: 41,523 hours analyzed
   NO_4_SE_2: 41,523 hours analyzed
   NO_4_FI: 41,523 hours analyzed

2. WRONG-DIRECTION FLOWS
   NO_3_SE_2      : 10.3% of hours
   NO_4_SE_2      : 7.6% of hours
   NO_1_SE_3      : 7.5% of hours
   NO_4_FI        : 7.4% of hours
   NO_2_DK_1      : 7.3% of hours
   NO_4_SE_1      : 5.3% of hours
   NO_2_DE_LU     : 4.1% of hours
   NO_2_NL        : 1.6% of hours

3. MEAN PRICE SPREADS (NO minus Foreign)
   NO_1_SE_3      : +21.95 EUR/MWh
   NO_2_DK_1      : -11.03 EUR/MWh
   NO_2_NL        : -21.63 EUR/MWh
   NO_2_DE_LU     : -21.45 EUR/MWh
   NO_3_SE_2      : -0.29 EUR/MWh
   NO_4_SE_1      : -12.20 EUR/MWh
   NO_4_SE_2      : -12.54 EUR/MWh
   NO_4_FI        : -48.02 EUR/MWh

4. CABLE UTILIZATION
   NO_1_SE_3      : 9.